In [ ]:
import pandas as pd
import geopandas as gpd
import pyproj
from tqdm import tqdm

import numpy as np
import plotly.express as px
import plotly.graph_objects as go
import plotly.graph_objs as go
import plotly.offline as offline
from plotly.subplots import make_subplots

import folium
from folium import plugins
from folium.plugins import HeatMap
from folium import FeatureGroup
from folium.plugins import HeatMapWithTime

from branca.colormap import linear
# 모든 열이 생략되지 않도록 설정
pd.set_option('display.max_columns', None)

In [ ]:
security_light = pd.read_csv('open/external_open/대구 보안등 정보.csv', encoding='cp949')
security_light

C:\Users\user\AppData\Local\Temp\ipykernel_26440\2934138998.py:1: DtypeWarning:

Columns (2) have mixed types. Specify dtype option on import or set low_memory=False.



보안등위치명  설치개수               소재지도로명주소               소재지지번주소  \
0              대명1동1     1       대구광역시 남구 현충로 155   대구광역시 남구 대명동 1722-4   
1              대명1동2     1   대구광역시 남구 현충로31길 10-1  대구광역시 남구 대명동 1723-11   
2              대명1동3     1    대구광역시 남구 현충로31길 9-8  대구광역시 남구 대명동 1722-56   
3              대명1동4     2  대구광역시 남구 현충로31길 19-11  대구광역시 남구 대명동 1722-41   
4              대명1동5     1   대구광역시 남구 현충로29길 22-2  대구광역시 남구 대명동 1721-22   
...              ...   ...                    ...                   ...   
71908     대봉2동 165-9     1                    NaN    대구광역시 중구 대봉동 165-9   
71909     대봉2동 88-85     1                    NaN    대구광역시 중구 대봉동 88-85   
71910    대봉2동 719-20     1                    NaN   대구광역시 중구 대봉동 719-20   
71911    대봉2동 738-13     1                    NaN   대구광역시 중구 대봉동 738-13   
71912  대봉2동 590-130대     1                    NaN  대구광역시 중구 대봉동 590-130   

              위도          경도    설치연도 설치형태  
0      35.846703  128.579803  2016.0  한전주  
1      35.846863  128.579406  2016.0  한전주  
2      35.846341  128.579342  2017.0  건축물  
3      35.846368  128.578922  2016.0  한전주  
4      35.845995  128.578858  2016.0  한전주  
...          ...         ...     ...  ...  
71908  35.857556  128.600023     NaN  한전주  
71909  35.859205  128.600046     NaN  한전주  
71910  35.859442  128.599627     NaN  한전주  
71911  35.858244  128.597614  2010.0  건축물  
71912  35.856805  128.596950  2016.0  한전주  

[71913 rows x 8 columns]

In [ ]:
kid_zone = pd.read_csv('open/external_open/대구 어린이 보호 구역 정보.csv', encoding='cp949')
kid_zone

시설종류     대상시설명                  소재지도로명주소              소재지지번주소         위도  \
0    초등학교    남도초등학교     대구광역시 남구 현충동길 74(대명동)    대구광역시 남구 대명동 1709  35.845027   
1    초등학교    영선초등학교       대구광역시 남구 영선길96(이천동)     대구광역시 남구 이천동 477  35.852901   
2    초등학교    성명초등학교  대구광역시 남구 성당로 30길 55(대명동)    대구광역시 남구 대명동 3050  35.845152   
3    초등학교    남덕초등학교     대구광역시 남구 앞산순환로 93길 33   대구광역시 남구 대명동 531-1  35.833042   
4    초등학교    대명초등학교          대구광역시 남구 대명로 110     대구광역시 남구 대명동 960  35.838869   
..    ...       ...                       ...                  ...        ...   
635  어린이집  남산교회어린이집          대구광역시 중구 관덕정길 16   대구광역시 중구 남산동 941-1  35.865040   
636  초등학교    대구초등학교        대구광역시 중구 명륜로23길 80      대구광역시 중구 봉산동 57  35.864037   
637  어린이집  대구삼성어린이집    대구광역시 중구 달구벌대로 2016-40   대구광역시 중구 남산동 153-2  35.864469   
638  어린이집  동화나라어린이집        대구광역시 중구 남산로3안길 20  대구광역시 중구 남산동 2623-6  35.860371   
639  어린이집   꿈나무어린이집         대구광역시 중구 남산로7길 35  대구광역시 중구 남산동 2508-2  35.858483   

             경도      관리기관명       관할경찰서명 CCTV설치여부  CCTV설치대수 보호구역도로폭     데이터기준일자  
0    128.581402      대구광역시        남부경찰서        Y       7.0     6~8  2020-03-23  
1    128.596014      대구광역시        남부경찰서        Y       8.0    6~10  2020-03-23  
2    128.570825      대구광역시        남부경찰서        Y      14.0    8~12  2020-03-23  
3    128.573949      대구광역시        남부경찰서        Y       6.0     6~8  2020-03-23  
4    128.568889      대구광역시        남부경찰서        Y       5.0    6~10  2020-03-23  
..          ...        ...          ...      ...       ...     ...         ...  
635  128.590565  대구광역시 중구청  대구광역시 중부경찰서        Y       5.0    6~10  2019-06-01  
636  128.595370  대구광역시 중구청  대구광역시 중부경찰서        Y      12.0    3~12  2019-06-01  
637  128.584301  대구광역시 중구청  대구광역시 중부경찰서        Y       2.0     7~8  2019-06-01  
638  128.577492  대구광역시 중구청  대구광역시 중부경찰서        Y       5.0     6~8  2019-06-01  
639  128.580584  대구광역시 중구청  대구광역시 중부경찰서        Y       4.0    7~11  2019-06-01  

[640 rows x 12 columns]

In [ ]:
# data1 = pd.read_csv('open/external_open/countrywide_accident_1.csv')
# data2 = pd.read_csv('open/external_open/countrywide_accident_2.csv')
# data3 = pd.read_csv('open/external_open/countrywide_accident_3.csv')
# data4 = pd.read_csv('open/external_open/countrywide_accident_4.csv')
# data = pd.concat([data1, data2, data3, data4]).reset_index(drop=True)
# data.to_csv('open/external_open/countrywide_accident.csv', index=False)

#### 대구광역시 격자데이터

In [ ]:
grid_500 = gpd.read_file('open/external_open/대구 빅데이터 마트 데이터/0. Base/대구광역시_500.gpkg')
grid_500 = grid_500.to_crs(epsg=4326)
grid_500

id          left           top         right        bottom  \
0       69  1.077033e+06  1.746587e+06  1.077533e+06  1.746087e+06   
1       70  1.077033e+06  1.746087e+06  1.077533e+06  1.745587e+06   
2       71  1.077033e+06  1.745587e+06  1.077533e+06  1.745087e+06   
3       72  1.077033e+06  1.745087e+06  1.077533e+06  1.744587e+06   
4       73  1.077033e+06  1.744587e+06  1.077533e+06  1.744087e+06   
...    ...           ...           ...           ...           ...   
3771  6746  1.113533e+06  1.766087e+06  1.114033e+06  1.765587e+06   
3772  6747  1.113533e+06  1.765587e+06  1.114033e+06  1.765087e+06   
3773  6748  1.113533e+06  1.765087e+06  1.114033e+06  1.764587e+06   
3774  6749  1.113533e+06  1.764587e+06  1.114033e+06  1.764087e+06   
3775  6750  1.113533e+06  1.764087e+06  1.114033e+06  1.763587e+06   

                                               geometry  
0     MULTIPOLYGON (((128.35675 35.70806, 128.35710 ...  
1     MULTIPOLYGON (((128.35180 35.70402, 128.35230 ...  
2     MULTIPOLYGON (((128.35148 35.69943, 128.35148 ...  
3     MULTIPOLYGON (((128.35205 35.69522, 128.35192 ...  
4     MULTIPOLYGON (((128.35344 35.69057, 128.35330 ...  
...                                                 ...  
3771  MULTIPOLYGON (((128.76093 35.88447, 128.76100 ...  
3772  MULTIPOLYGON (((128.75909 35.88007, 128.75897 ...  
3773  MULTIPOLYGON (((128.75953 35.87574, 128.75962 ...  
3774  MULTIPOLYGON (((128.75939 35.87123, 128.75933 ...  
3775  MULTIPOLYGON (((128.75982 35.86670, 128.75982 ...  

[3776 rows x 6 columns]

In [ ]:
# map 생성
m = folium.Map(location=[35.87285921915183, 128.5969619227697], zoom_start=12)

# GeoDataFrame을 순회하면서 Polygon을 지도에 추가
for idx, row in grid_500.iterrows():
    popup_text = f"{row['geometry']}"
    folium.GeoJson(
        row['geometry'].__geo_interface__,
        style_function=lambda feature, color='black': {'color': 'black', 'weight': 1}
    ).add_to(m).add_child(folium.Popup(popup_text, max_width=100))

# 맵 출력
m

#### 대구광역시 수치표고

In [ ]:
digital_elevation_500 = gpd.read_file('open/external_open/대구 빅데이터 마트 데이터/1. 환경/8. 수치표고/수치표고_500.gpkg')
digital_elevation_500 = digital_elevation_500.to_crs(epsg=4326)
#digital_elevation_500['NUMPOINTS'] = digital_elevation_500['NUMPOINTS'].astype(int)
digital_elevation_500

In [ ]:
# map 생성
m = folium.Map(location=[35.87285921915183, 128.5969619227697], zoom_start=12)

folium.TileLayer('openstreetmap', overlay=False).add_to(m)
m_elevation = folium.FeatureGroup(name="수치표고", overlay=False)
# GeoDataFrame을 순회하면서 Polygon을 지도에 추가
for idx, row in digital_elevation_500.iterrows():
    popup_text = f"{row['DN_mean']}"
    
    # 그라데이션을 위한 colormap 정의
    colormap = linear.YlOrRd_09.scale(4.25, 1062.83871)
    
    # fill color를 그라데이션으로 지정
    fill_color = colormap(row['DN_mean'])
    folium.GeoJson(
        row['geometry'].__geo_interface__,
        style_function=lambda feature, color=fill_color: {'fillColor': color, 'color': 'black', 'weight': 0.5}
    ).add_to(m_elevation).add_child(folium.Popup(popup_text, max_width=100))

# colormap을 맵에 추가 (선택사항)
colormap.add_to(m)

m_elevation.add_to(m)

# LayerControl을 사용하여 연도 선택
folium.LayerControl(collapsed=False).add_to(m)
# 맵 출력
m

In [ ]:
parkinglot = pd.read_csv('open/external_open/대구 주차장 정보.csv', encoding='cp949')
parkinglot

#### 생활폐기물 불법투기

In [ ]:
waste_500 = gpd.read_file('open/external_open/대구 빅데이터 마트 데이터/1. 환경/4. 생활폐기물불법투기/생활폐기물불법투기장소_500.gpkg')
waste_500 = waste_500.to_crs(epsg=4326)
waste_500['NUMPOINTS'] = waste_500['NUMPOINTS'].astype(int)
waste_500

id          left           top         right        bottom  NUMPOINTS  \
0       69  1.077033e+06  1.746587e+06  1.077533e+06  1.746087e+06          0   
1       70  1.077033e+06  1.746087e+06  1.077533e+06  1.745587e+06          0   
2       71  1.077033e+06  1.745587e+06  1.077533e+06  1.745087e+06          0   
3       72  1.077033e+06  1.745087e+06  1.077533e+06  1.744587e+06          0   
4       73  1.077033e+06  1.744587e+06  1.077533e+06  1.744087e+06          0   
...    ...           ...           ...           ...           ...        ...   
3771  6746  1.113533e+06  1.766087e+06  1.114033e+06  1.765587e+06          0   
3772  6747  1.113533e+06  1.765587e+06  1.114033e+06  1.765087e+06          0   
3773  6748  1.113533e+06  1.765087e+06  1.114033e+06  1.764587e+06          0   
3774  6749  1.113533e+06  1.764587e+06  1.114033e+06  1.764087e+06          0   
3775  6750  1.113533e+06  1.764087e+06  1.114033e+06  1.763587e+06          0   

                                               geometry  
0     MULTIPOLYGON (((128.35675 35.70806, 128.35710 ...  
1     MULTIPOLYGON (((128.35180 35.70402, 128.35230 ...  
2     MULTIPOLYGON (((128.35148 35.69943, 128.35148 ...  
3     MULTIPOLYGON (((128.35205 35.69522, 128.35192 ...  
4     MULTIPOLYGON (((128.35344 35.69057, 128.35330 ...  
...                                                 ...  
3771  MULTIPOLYGON (((128.76093 35.88447, 128.76100 ...  
3772  MULTIPOLYGON (((128.75909 35.88007, 128.75897 ...  
3773  MULTIPOLYGON (((128.75953 35.87574, 128.75962 ...  
3774  MULTIPOLYGON (((128.75939 35.87123, 128.75933 ...  
3775  MULTIPOLYGON (((128.75982 35.86670, 128.75982 ...  

[3776 rows x 7 columns]

In [ ]:
waste_500['NUMPOINTS'].unique()

array([ 0,  1,  2,  3,  6,  4,  8, 12,  7,  5, 10, 18,  9, 11, 16, 15, 17,
       23, 21, 14, 22, 13, 19])

In [ ]:
# map 생성
m = folium.Map(location=[35.87285921915183, 128.5969619227697], zoom_start=12)

m_waste = folium.FeatureGroup(name="생활폐기물 불법투기 장소 개수", overlay=False)
# GeoDataFrame을 순회하면서 Polygon을 지도에 추가
for idx, row in waste_500.iterrows():
    popup_text = f"{row['NUMPOINTS']}"
    
    # 그라데이션을 위한 colormap 정의
    colormap = linear.YlOrRd_09.scale(0, 23)
    
    # fill color를 그라데이션으로 지정
    fill_color = colormap(row['NUMPOINTS'])
    folium.GeoJson(
        row['geometry'].__geo_interface__,
        style_function=lambda feature, color=fill_color: {'fillColor': color, 'color': 'black', 'weight': 1}
    ).add_to(m_waste).add_child(folium.Popup(popup_text, max_width=100))

# colormap을 맵에 추가 (선택사항)
colormap.add_to(m)

m_waste.add_to(m)

# LayerControl을 사용하여 연도 선택
folium.LayerControl(collapsed=False).add_to(m)
# 맵 출력
m

#### 대구광역시 문화시설 통합 및 격자매핑(도서관, 공연시설, 미술관, 박물관, 영화관)

In [ ]:
# 도서관데이터 로드
library_500 = gpd.read_file('open/external_open/대구 빅데이터 마트 데이터/2. 문화/1. 도서관/공공도서관_500.gpkg')
library_500 = library_500.to_crs(epsg=4326)
library_500['NUMPOINTS'] = library_500['NUMPOINTS'].astype(int)
library_500.rename(columns={'NUMPOINTS':'library'}, inplace=True)

# 공연장데이터 로드
venue_500 = gpd.read_file('open/external_open/대구 빅데이터 마트 데이터/2. 문화/2. 공연시설/공연장_500.gpkg')
venue_500 = venue_500.to_crs(epsg=4326)
venue_500['NUMPOINTS'] = venue_500['NUMPOINTS'].astype(int)
venue_500.rename(columns={'NUMPOINTS':'venue'}, inplace=True)

# 미술관데이터 로드
artmuseum_500 = gpd.read_file('open/external_open/대구 빅데이터 마트 데이터/2. 문화/3. 미술관/미술관_500.gpkg')
artmuseum_500 = artmuseum_500.to_crs(epsg=4326)
artmuseum_500['NUMPOINTS'] = artmuseum_500['NUMPOINTS'].astype(int)
artmuseum_500.rename(columns={'NUMPOINTS':'artmuseum'}, inplace=True)

# 박물관데이터 로드
museum_500 = gpd.read_file('open/external_open/대구 빅데이터 마트 데이터/2. 문화/4. 박물관/박물관_500.gpkg')
museum_500 = museum_500.to_crs(epsg=4326)
museum_500['NUMPOINTS'] = museum_500['NUMPOINTS'].astype(int)
museum_500.rename(columns={'NUMPOINTS':'museum'}, inplace=True)

# 영화관데이터 로드
theater_500 = gpd.read_file('open/external_open/대구 빅데이터 마트 데이터/2. 문화/5. 영화관/영화관_500.gpkg')
theater_500 = theater_500.to_crs(epsg=4326)
theater_500['NUMPOINTS'] = theater_500['NUMPOINTS'].astype(int)
theater_500.rename(columns={'NUMPOINTS':'theater'}, inplace=True)

culture_tot = pd.concat([library_500.iloc[:,0], library_500.iloc[:,5], venue_500.iloc[:,5], artmuseum_500.iloc[:,5], museum_500.iloc[:,5], theater_500.iloc[:,5], library_500.iloc[:,6]], axis=1)
culture_tot

id  library  venue  artmuseum  museum  theater  \
0       69        0      0          0       0        0   
1       70        0      0          0       0        0   
2       71        0      0          0       0        0   
3       72        0      0          0       0        0   
4       73        0      0          0       0        0   
...    ...      ...    ...        ...     ...      ...   
3771  6746        0      0          0       0        0   
3772  6747        0      0          0       0        0   
3773  6748        0      0          0       0        0   
3774  6749        0      0          0       0        0   
3775  6750        0      0          0       0        0   

                                               geometry  
0     MULTIPOLYGON (((128.35675 35.70806, 128.35710 ...  
1     MULTIPOLYGON (((128.35180 35.70402, 128.35230 ...  
2     MULTIPOLYGON (((128.35148 35.69943, 128.35148 ...  
3     MULTIPOLYGON (((128.35205 35.69522, 128.35192 ...  
4     MULTIPOLYGON (((128.35344 35.69057, 128.35330 ...  
...                                                 ...  
3771  MULTIPOLYGON (((128.76093 35.88447, 128.76100 ...  
3772  MULTIPOLYGON (((128.75909 35.88007, 128.75897 ...  
3773  MULTIPOLYGON (((128.75953 35.87574, 128.75962 ...  
3774  MULTIPOLYGON (((128.75939 35.87123, 128.75933 ...  
3775  MULTIPOLYGON (((128.75982 35.86670, 128.75982 ...  

[3776 rows x 7 columns]

In [ ]:
culture_tot['tot'] = culture_tot.iloc[:,1:6].sum(axis=1) # 문화시설 통합

# map 생성
m = folium.Map(location=[35.87285921915183, 128.5969619227697], zoom_start=12)

folium.TileLayer('openstreetmap', overlay=False).add_to(m)
m_culture = folium.FeatureGroup(name="문화시설", overlay=False)
# GeoDataFrame을 순회하면서 Polygon을 지도에 추가
for idx, row in culture_tot.iterrows():
    popup_text = f"{row['tot']}"
    
    # 그라데이션을 위한 colormap 정의
    colormap = linear.YlOrRd_09.scale(culture_tot['tot'].min(), culture_tot['tot'].max())
    
    # fill color를 그라데이션으로 지정
    fill_color = colormap(row['tot'])
    folium.GeoJson(
        row['geometry'].__geo_interface__,
        style_function=lambda feature, color=fill_color: {'fillColor': color, 'color': 'black', 'weight': 0.5}
    ).add_to(m_culture).add_child(folium.Popup(popup_text, max_width=100))

# colormap을 맵에 추가 (선택사항)
colormap.add_to(m)

m_culture.add_to(m)

# LayerControl을 사용하여 연도 선택
folium.LayerControl(collapsed=False).add_to(m)
# 맵 출력
m

#### 대구광역시 복지시설 통합 및 격자매핑(행정복지센터, 노인복지관, 경로당, 노인요양시설)

In [ ]:
# 행정복지센터데이터 로드
adcenter_500 = gpd.read_file('open/external_open/대구 빅데이터 마트 데이터/3. 복지/1. 행정복지센터/행정복지센터_500.gpkg')
adcenter_500 = adcenter_500.to_crs(epsg=4326)
adcenter_500['NUMPOINTS'] = adcenter_500['NUMPOINTS'].astype(int)
adcenter_500.rename(columns={'NUMPOINTS':'adcenter'}, inplace=True)

# 노인복지관데이터 로드
senwelfare_500 = gpd.read_file('open/external_open/대구 빅데이터 마트 데이터/3. 복지/2. 노인복지관/노인복지관_500.gpkg')
senwelfare_500 = senwelfare_500.to_crs(epsg=4326)
senwelfare_500['NUMPOINTS'] = senwelfare_500['NUMPOINTS'].astype(int)
senwelfare_500.rename(columns={'NUMPOINTS':'senwelfare'}, inplace=True)

# 경로당데이터 로드
sencenter_500 = gpd.read_file('open/external_open/대구 빅데이터 마트 데이터/3. 복지/3. 경로당/경로당_500.gpkg')
sencenter_500 = sencenter_500.to_crs(epsg=4326)
sencenter_500['NUMPOINTS'] = sencenter_500['NUMPOINTS'].astype(int)
sencenter_500.rename(columns={'NUMPOINTS':'sencenter'}, inplace=True)

# 노인요양시설데이터 로드
sanatorium_500 = gpd.read_file('open/external_open/대구 빅데이터 마트 데이터/3. 복지/4. 노인요양시설/노인요양시설_500.gpkg')
sanatorium_500 = sanatorium_500.to_crs(epsg=4326)
sanatorium_500['NUMPOINTS'] = sanatorium_500['NUMPOINTS'].astype(int)
sanatorium_500.rename(columns={'NUMPOINTS':'sanatorium'}, inplace=True)

welfare_tot = pd.concat([adcenter_500.iloc[:,0], adcenter_500.iloc[:,5], senwelfare_500.iloc[:,5], sencenter_500.iloc[:,5], sanatorium_500.iloc[:,5], library_500.iloc[:,6]], axis=1)
welfare_tot

id  adcenter  senwelfare  sencenter  sanatorium  \
0       69         0           0          0           0   
1       70         0           0          0           0   
2       71         0           0          0           0   
3       72         0           0          0           0   
4       73         0           0          0           0   
...    ...       ...         ...        ...         ...   
3771  6746         0           0          0           0   
3772  6747         0           0          0           0   
3773  6748         0           0          0           0   
3774  6749         0           0          0           0   
3775  6750         0           0          0           0   

                                               geometry  
0     MULTIPOLYGON (((128.35675 35.70806, 128.35710 ...  
1     MULTIPOLYGON (((128.35180 35.70402, 128.35230 ...  
2     MULTIPOLYGON (((128.35148 35.69943, 128.35148 ...  
3     MULTIPOLYGON (((128.35205 35.69522, 128.35192 ...  
4     MULTIPOLYGON (((128.35344 35.69057, 128.35330 ...  
...                                                 ...  
3771  MULTIPOLYGON (((128.76093 35.88447, 128.76100 ...  
3772  MULTIPOLYGON (((128.75909 35.88007, 128.75897 ...  
3773  MULTIPOLYGON (((128.75953 35.87574, 128.75962 ...  
3774  MULTIPOLYGON (((128.75939 35.87123, 128.75933 ...  
3775  MULTIPOLYGON (((128.75982 35.86670, 128.75982 ...  

[3776 rows x 6 columns]

In [ ]:
welfare_tot['tot'] = welfare_tot.iloc[:,1:5].sum(axis=1) # 문화시설 통합

# map 생성
m = folium.Map(location=[35.87285921915183, 128.5969619227697], zoom_start=12)

m_culture = folium.FeatureGroup(name="복지시설", overlay=False)
# GeoDataFrame을 순회하면서 Polygon을 지도에 추가
for idx, row in welfare_tot.iterrows():
    popup_text = f"{row['tot']}"
    
    # 그라데이션을 위한 colormap 정의
    colormap = linear.YlOrRd_09.scale(welfare_tot['tot'].min(), welfare_tot['tot'].max())
    
    # fill color를 그라데이션으로 지정
    fill_color = colormap(row['tot'])
    folium.GeoJson(
        row['geometry'].__geo_interface__,
        style_function=lambda feature, color=fill_color: {'fillColor': color, 'color': 'black', 'weight': 0.5}
    ).add_to(m_culture).add_child(folium.Popup(popup_text, max_width=100))

# colormap을 맵에 추가 (선택사항)
colormap.add_to(m)

m_culture.add_to(m)

# LayerControl을 사용하여 연도 선택
folium.LayerControl(collapsed=False).add_to(m)
# 맵 출력
m

#### 대구광역시 소방관서

In [ ]:
# 소방관서데이터 로드
firestation_500 = gpd.read_file('open/external_open/대구 빅데이터 마트 데이터/3. 복지/12. 소방관서/소방관서_500.gpkg')
firestation_500 = firestation_500.to_crs(epsg=4326)
firestation_500['NUMPOINTS'] = firestation_500['NUMPOINTS'].astype(int)
firestation_500.rename(columns={'NUMPOINTS':'firestation'}, inplace=True)
firestation_500

id          left           top         right        bottom  \
0       69  1.077033e+06  1.746587e+06  1.077533e+06  1.746087e+06   
1       70  1.077033e+06  1.746087e+06  1.077533e+06  1.745587e+06   
2       71  1.077033e+06  1.745587e+06  1.077533e+06  1.745087e+06   
3       72  1.077033e+06  1.745087e+06  1.077533e+06  1.744587e+06   
4       73  1.077033e+06  1.744587e+06  1.077533e+06  1.744087e+06   
...    ...           ...           ...           ...           ...   
3771  6746  1.113533e+06  1.766087e+06  1.114033e+06  1.765587e+06   
3772  6747  1.113533e+06  1.765587e+06  1.114033e+06  1.765087e+06   
3773  6748  1.113533e+06  1.765087e+06  1.114033e+06  1.764587e+06   
3774  6749  1.113533e+06  1.764587e+06  1.114033e+06  1.764087e+06   
3775  6750  1.113533e+06  1.764087e+06  1.114033e+06  1.763587e+06   

      firestation                                           geometry  
0               0  MULTIPOLYGON (((128.35675 35.70806, 128.35710 ...  
1               0  MULTIPOLYGON (((128.35180 35.70402, 128.35230 ...  
2               0  MULTIPOLYGON (((128.35148 35.69943, 128.35148 ...  
3               0  MULTIPOLYGON (((128.35205 35.69522, 128.35192 ...  
4               0  MULTIPOLYGON (((128.35344 35.69057, 128.35330 ...  
...           ...                                                ...  
3771            0  MULTIPOLYGON (((128.76093 35.88447, 128.76100 ...  
3772            0  MULTIPOLYGON (((128.75909 35.88007, 128.75897 ...  
3773            0  MULTIPOLYGON (((128.75953 35.87574, 128.75962 ...  
3774            0  MULTIPOLYGON (((128.75939 35.87123, 128.75933 ...  
3775            0  MULTIPOLYGON (((128.75982 35.86670, 128.75982 ...  

[3776 rows x 7 columns]

In [ ]:
# map 생성
m = folium.Map(location=[35.87285921915183, 128.5969619227697], zoom_start=12)

m_culture = folium.FeatureGroup(name="소방관서", overlay=False)
# GeoDataFrame을 순회하면서 Polygon을 지도에 추가
for idx, row in firestation_500.iterrows():
    popup_text = f"{row['firestation']}"
    
    # 그라데이션을 위한 colormap 정의
    colormap = linear.YlOrRd_09.scale(firestation_500['firestation'].min(), firestation_500['firestation'].max())
    
    # fill color를 그라데이션으로 지정
    fill_color = colormap(row['firestation'])
    folium.GeoJson(
        row['geometry'].__geo_interface__,
        style_function=lambda feature, color=fill_color: {'fillColor': color, 'color': 'black', 'weight': 0.5}
    ).add_to(m_culture).add_child(folium.Popup(popup_text, max_width=100))

# colormap을 맵에 추가 (선택사항)
colormap.add_to(m)

m_culture.add_to(m)

# LayerControl을 사용하여 연도 선택
folium.LayerControl(collapsed=False).add_to(m)
# 맵 출력
m

#### 대구광역시 나드리콜(굳이...??)

In [ ]:
# 소방관서데이터 로드
traffic_500 = gpd.read_file('open/external_open/대구 빅데이터 마트 데이터/3. 복지/13. 나드리콜/목적지분류_교통시설_500.gpkg')
traffic_500 = traffic_500.to_crs(epsg=4326)
traffic_500['NUMPOINTS'] = traffic_500['NUMPOINTS'].astype(int)
traffic_500.rename(columns={'NUMPOINTS':'traffic'}, inplace=True)
traffic_500